## Class based dashboard 

Merging approaches from the original approach with reactive functions(11_11_20_holoviz_gliderdash), with the class based restructing that Don did (holoviz_gliderdash_class), with the NYC taxi example (https://examples.pyviz.org/datashader_dashboard/dashboard.html). 

In [1]:
import hvplot.xarray 
import numpy as np
import panel as pn
import xarray as xr
import holoviews as hv

### Load Data

In [3]:
# load data 

# open Surface fields
fname_SSH = "../../../glider-panel-demo/data/SSH_sogos.nc"
fname_FSLE = "../../../glider-panel-demo/data/FSLE_sogos.nc"

ds_ssh = xr.open_dataset(fname_SSH)
ds_fsle = xr.open_dataset(fname_FSLE)

# Create variables for vectors
ds_ssh['mag'] = np.sqrt(ds_ssh.ugos**2 + ds_ssh.vgos**2)
ds_ssh['angle'] = (np.pi/2.) - np.arctan2(ds_ssh.ugos/ds_ssh['mag'], 
                                          ds_ssh.vgos/ds_ssh['mag'])


# convert to a time axis that is easier to handle 
# might make sense to figure out how to directly use the dates. 
days = ds_ssh.time - np.datetime64('2019-01-01')
ds_ssh['days'] = (days / np.timedelta64(1, 'D'))

days = ds_fsle.time - np.datetime64('2019-01-01')
ds_fsle['days'] = (days / np.timedelta64(1, 'D'))

In [4]:
# open glider files
glid_folder = '../../../glider-panel-demo/data/'

## all this next bit till the averaging is only being used for knowing the 
# position at each dive. Might be more consistent to merge this with the files
# names *_grid. 
ds_659 = xr.load_dataset(glid_folder + 'sg659/CTD_659.nc')
ds_660 = xr.load_dataset(glid_folder + 'sg660/CTD_660.nc')

# easier to work with a days variable that is a float rather than datenum
days = ds_659.time - np.datetime64('2019-01-01')
ds_659['days'] = (days / np.timedelta64(1, 'D'))

days = ds_660.time - np.datetime64('2019-01-01')
ds_660['days'] = (days / np.timedelta64(1, 'D'))

# Group and average by dives so that plotting of positions is fast
ds_659_av = ds_659.groupby('dives').mean()
ds_660_av = ds_660.groupby('dives').mean()

ds_659_av = ds_659_av.drop('dives')
ds_660_av = ds_660_av.drop('dives')

# load in a gridded version of the glides
ds_659_grid = xr.load_dataset(glid_folder + '659_grid.nc')
ds_660_grid = xr.load_dataset(glid_folder + '660_grid.nc')

## Glider panel

from collections import OrderedDict as odict
from holoviews import streams
import param

In [24]:
glider_nums = ['sg659', 'sg660']
glider_vars = list(ds_659_grid.keys())

In [39]:
var_select_map = {
            'spice': {
                'bin_range': (-0.7, 0.02),
                'cmap_sel': 'RdBu_r'
            },
            'salinity': {
                'bin_range': (33.75, 35),
                'cmap_sel': 'RdBu_r'
            },
            'temperature': {
                'bin_range': (0,4),
                'cmap_sel': 'RdBu_r'
            },
            'potdens': {
                'bin_range': (1026.8, 1027.8),
                'cmap_sel': 'RdBu_r'
            }
        }
glider_map = {
            'sg659': ds_659_grid,
            'sg660': ds_660_grid
        }

### Simple
works. 

In [70]:
# simple implementation
# In this style, anytime anything changes, the entire plot is plotted

class GliderPlot(param.Parameterized):
    glider_num = param.Selector(glider_nums, label='Glider Num#')
    glider_var = param.Selector(glider_vars, label='Glider Variable')
    
    time_slider = param.Range(label='Days [YTD] 2019', 
                             bounds=(115, 210), 
                             default=(115, 130))
    def view(self):
        image = glider_map[self.glider_num][self.glider_var].hvplot.image(
                                        rasterize=True,
                                        cmap=var_select_map[self.glider_var]['cmap_sel'], 
                                        flip_yaxis=True, 
                                        clim=var_select_map[self.glider_var]['bin_range']
        ).apply.opts(xlim = self.time_slider
        ).hist(
                                         bin_range = var_select_map[self.glider_var]['bin_range'])
        
        contour = glider_map[self.glider_num]['potdens'].hvplot.contour(flip_yaxis=True, 
                                                                     levels=np.linspace(1026.8, 1027.8,11)
                                                                     ).apply.opts(xlim = self.time_slider)
        return image*contour
        

In [68]:
test = GliderPlot()

In [69]:
pn.Column(test.param, test.view)

Column
    [0] Column(margin=5, name='GliderPlot', width=300)
        [0] StaticText(value='<b>GliderPlot</b>')
        [1] Select(name='Glider Num#', options=OrderedDict([('sg659', ...]), value='sg659')
        [2] Select(name='Glider Variable', options=OrderedDict([('temperature...]), value='temperature')
        [3] RangeSlider(end=210, name='Days [YTD] 2019', start=115, step=1, value=(115, 130), value_throttled=(115, 130))
    [1] ParamMethod(method)

### Complex 

In [108]:
class GliderPlot2(param.Parameterized):
    glider_num = param.Selector(glider_nums, label='Glider Num#')
    glider_var = param.Selector(glider_vars, label='Glider Variable')
    
    time_slider = param.Range(label='Days [YTD] 2019', 
                             bounds=(115, 210), 
                             default=(115, 130))
    
    density_range = param.Range(label='Density range', bounds=(1026.8, 1027.9))
    density_gradation = param.Integer(label='Density levels', default=11, bounds=(2, 21))
    
    @pn.depends('density_range', 'density_gradation')
    def density_contours(self):
        print(self.density_range.bounds)
        contour = glider_map[self.glider_num]['potdens'].hvplot.contour(flip_yaxis=True, 
                                                                     levels=np.linspace(self.density_range.bounds[0],
                                                                                        self.density_range.bounds[1],
                                                                                        self.density_gradation.default)
                                                                       )
        return contour
    
    def viewable(self):
        image = glider_map[self.glider_num][self.glider_var].hvplot.image(
                                        rasterize=True,
                                        cmap=var_select_map[self.glider_var]['cmap_sel'], 
                                        flip_yaxis=True, 
                                        clim=var_select_map[self.glider_var]['bin_range']
                ).apply.opts(xlim = self.time_slider
                    ).hist(
                                         bin_range = var_select_map[self.glider_var]['bin_range'])
        
        return image

In [109]:
test2 = GliderPlot2()

In [115]:
test2.density_range.bounds

AttributeError: 'NoneType' object has no attribute 'bounds'

In [114]:
density_range = param.Range(label='Density range', bounds=(1026.8, 1027.9))
density_range.bounds

(1026.8, 1027.9)

AttributeError: 'NoneType' object has no attribute 'bounds'

In [110]:
pn.Column(test2.param, test2.viewable)

Column
    [0] Column(margin=5, name='GliderPlot', width=300)
        [0] StaticText(value='<b>GliderPlot</b>')
        [1] Select(name='Glider Num#', options=OrderedDict([('sg659', ...]), value='sg659')
        [2] Select(name='Glider Variable', options=OrderedDict([('temperature...]), value='temperature')
        [3] RangeSlider(end=210, name='Days [YTD] 2019', start=115, step=1, value=(115, 130), value_throttled=(115, 130))
        [4] RangeSlider(end=1027.9, name='Density range', start=1026.8, value=(1026.8, 1027.9), value_throttled=(1026.8, 1027.9))
        [5] IntSlider(end=21, name='Density levels', start=2, value=11, value_throttled=11)
    [1] ParamMethod(method)